In [1]:
import numpy as np
from numpy import array
import pandas as pd
import matplotlib.pyplot as plt
import string
import os
from PIL import Image
import glob
from pickle import dump, load
from time import time
from keras.preprocessing import sequence
from keras.models import Sequential
from keras.layers import LSTM, Embedding, TimeDistributed, Dense, RepeatVector,\
                         Activation, Flatten, Reshape, concatenate, Dropout, BatchNormalization
from tensorflow.keras.optimizers import Adam, RMSprop
from keras.layers.wrappers import Bidirectional
from keras.layers.merge import add
from keras.applications.inception_v3 import InceptionV3
from keras.preprocessing import image
from keras.models import Model
from keras import Input, layers
from keras import optimizers
from keras.applications.inception_v3 import preprocess_input
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from nltk.translate.meteor_score import meteor_score
from nltk.translate.bleu_score import sentence_bleu, corpus_bleu
from keras import callbacks
from keras import optimizers
import json
from helper import *
from config import *
from dataloader import *
from model import *

In [2]:
data = DataLoader(config_mixed_flickr8k_30k)

Train dataset
Train dataset loaded: 6000
Photos: train=6000
{'1000268201_693b08cb0e': ['A child in a pink dress is climbing up a set of stairs in an entry way .', 'A girl going into a wooden building .', 'A little girl climbing into a wooden playhouse .', 'A little girl climbing the stairs to her playhouse .', 'A little girl in a pink dress going into a wooden cabin .'], '1001773457_577c3a7d70': ['A black dog and a spotted dog are fighting', 'A black dog and a tri-colored dog playing with each other on the road .', 'A black dog and a white dog with brown spots are staring at each other in the street .', 'Two dogs of different breeds looking at each other on the road .', 'Two dogs on pavement moving toward each other .'], '1002674143_1b742ab4b8': ['A little girl covered in paint sits in front of a painted rainbow with her hands in a bowl .', 'A little girl is sitting in front of a large painted rainbow .', 'A small girl in the grass plays with fingerpaints in front of a white canvas wit

Save descriptions in separate file
save desc


/home/wisla/projects/test-framework/dataloader.py:43: SyntaxWarning: "is" with a literal. Did you mean "=="?
  if config["data_name"] is "flickr8k":
/home/wisla/projects/test-framework/dataloader.py:45: SyntaxWarning: "is" with a literal. Did you mean "=="?
  if config["data_name"] is "flickr8k_polish":
/home/wisla/projects/test-framework/dataloader.py:47: SyntaxWarning: "is" with a literal. Did you mean "=="?
  elif config["data_name"] is "flickr30k":
/home/wisla/projects/test-framework/dataloader.py:49: SyntaxWarning: "is" with a literal. Did you mean "=="?
  elif config["data_name"] is "flickr30k_polish":
/home/wisla/projects/test-framework/dataloader.py:51: SyntaxWarning: "is" with a literal. Did you mean "=="?
  elif config["data_name"] is "aide":
/home/wisla/projects/test-framework/dataloader.py:53: SyntaxWarning: "is" with a literal. Did you mean "=="?
  elif config["data_name"] is "coco14":
/home/wisla/projects/test-framework/dataloader.py:55: SyntaxWarning: "is" with a literal

NameError: name 'descriptions' is not defined

In [4]:
data.train_descriptions

{'1000268201_693b08cb0e': ['startseq a child in a pink dress is climbing up a set of stairs in an entry way endseq',
  'startseq a girl going into a wooden building endseq',
  'startseq a little girl climbing into a wooden playhouse endseq',
  'startseq a little girl climbing the stairs to her playhouse endseq',
  'startseq a little girl in a pink dress going into a wooden cabin endseq'],
 '1001773457_577c3a7d70': ['startseq a black dog and a spotted dog are fighting endseq',
  'startseq a black dog and a tricolored dog playing with each other on the road endseq',
  'startseq a black dog and a white dog with brown spots are staring at each other in the street endseq',
  'startseq two dogs of different breeds looking at each other on the road endseq',
  'startseq two dogs on pavement moving toward each other endseq'],
 '1002674143_1b742ab4b8': ['startseq a little girl covered in paint sits in front of a painted rainbow with her hands in a bowl endseq',
  'startseq a little girl is sitti

In [5]:
data.train_descriptions2

{'1000268201_693b08cb0e': ['startseq a child in a pink dress is climbing up a set of stairs in an entry way endseq',
  'startseq a girl going into a wooden building endseq',
  'startseq a little girl climbing into a wooden playhouse endseq',
  'startseq a little girl climbing the stairs to her playhouse endseq',
  'startseq a little girl in a pink dress going into a wooden cabin endseq'],
 '1001773457_577c3a7d70': ['startseq a black dog and a spotted dog are fighting endseq',
  'startseq a black dog and a tricolored dog playing with each other on the road endseq',
  'startseq a black dog and a white dog with brown spots are staring at each other in the street endseq',
  'startseq two dogs of different breeds looking at each other on the road endseq',
  'startseq two dogs on pavement moving toward each other endseq'],
 '1002674143_1b742ab4b8': ['startseq a little girl covered in paint sits in front of a painted rainbow with her hands in a bowl endseq',
  'startseq a little girl is sitti

In [8]:
print(data.descriptions)

{'1000268201_693b08cb0e': ['a child in a pink dress is climbing up a set of stairs in an entry way', 'a girl going into a wooden building', 'a little girl climbing into a wooden playhouse', 'a little girl climbing the stairs to her playhouse', 'a little girl in a pink dress going into a wooden cabin'], '1001773457_577c3a7d70': ['a black dog and a spotted dog are fighting', 'a black dog and a tricolored dog playing with each other on the road', 'a black dog and a white dog with brown spots are staring at each other in the street', 'two dogs of different breeds looking at each other on the road', 'two dogs on pavement moving toward each other'], '1002674143_1b742ab4b8': ['a little girl covered in paint sits in front of a painted rainbow with her hands in a bowl', 'a little girl is sitting in front of a large painted rainbow', 'a small girl in the grass plays with fingerpaints in front of a white canvas with a rainbow on it', 'there is a girl with pigtails sitting in front of a rainbow pa

In [3]:
model=ModelImpl(data)

Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            [(None, 37)]         0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 2048)]       0                                            
__________________________________________________________________________________________________
embedding (Embedding)           (None, 37, 199)      329345      input_3[0][0]                    
__________________________________________________________________________________________________
dropout (Dropout)               (None, 2048)         0           input_2[0][0]                    
____________________________________________________________________________________________

In [4]:
model.train()

In [5]:
model.evaluate()


tokenization...
setting up scorers...
computing Bleu score...
{'testlen': 10146, 'reflen': 9779, 'guess': [10146, 9146, 8146, 7146], 'correct': [5727, 2231, 706, 231]}
ratio: 1.037529399734018
Bleu_1: 0.564
Bleu_2: 0.371
Bleu_3: 0.229
Bleu_4: 0.140
computing METEOR score...
METEOR: 0.174
computing Rouge score...
ROUGE_L: 0.421
computing CIDEr score...
CIDEr: 0.346
computing SPICE score...
SPICE: 0.103
computing WMD score...
WMD: 0.115
results/flickr8k.json
{'Bleu_1': 0.564458900059081, 'Bleu_2': 0.37106530494328893, 'Bleu_3': 0.22851795621339666, 'Bleu_4': 0.14014496209011834, 'METEOR': 0.17369730864845484, 'ROUGE_L': 0.42085736478293007, 'CIDEr': 0.34590795694298243, 'SPICE': 0.10303311810813434, 'WMD': 0.11477941306146561}
